In [1]:
import requests, pandas as pd, numpy as np
from requests import session
from bs4 import BeautifulSoup

In [2]:
url='http://www.omnibus.ro/index.php/hu/szekelyfoldi-top-listak/arbevetel/also-haromszek-2015-2018#oldal'
r = requests.get(url)

for c in r.cookies:
    print(c.name, c.value)

__cfduid ddf927e7801beda5fe82f1d16dfea29e81578227078
PHPSESSID 37tq2cosotem3rha99bjdhd280


In [23]:
url='http://www.omnibus.ro/index.php/hu/szekelyfoldi-top-listak/kozbirtokossag/top25-kozbirtokossag-2019#oldal'
with session() as c:
    response = c.get(url)
    #print(response.headers)
    #print(response.text)
    df=pd.read_html(response.text)[1]
    df.columns=list(df.loc[0])
    df=df.loc[2:]
    #df=df[df.columns[1:-1]]
    df=df.loc[list(df.index)[:-1]]
    #df['nr']=df.index

soup = BeautifulSoup(response.content)
links=soup.findAll('table')[3].findAll('a')

In [25]:
coords=[]
kws=[]
cms=[]
for i in range(len(links)):
    print(i,)
    r=requests.get(links[i]['href'])
    g=repr(r.content)
    coord_start=g.find('GLatLng')
    coord_end=coord_start+g[coord_start:].find(')')
    coord=g[coord_start+len('GLatLng')+1:coord_end].split(',')
    kw_start=g.find('<meta name="keywords')
    kw_end=kw_start+g[kw_start:].find('/>')
    kw=g[kw_start+len('<meta name="keywords" content="'):kw_end].split(',')
    kw=[i.strip() for i in kw]
    cm_start=g.find('<b>C&iacute;m:</b>')
    cm_end=cm_start+g[cm_start:].find('<br>')
    cm=g[cm_start+len('<b>C&iacute;m:</b>'):cm_end].strip()

    coords.append(coord)
    kws.append(kw)
    cms.append(cm)

df=df[:len(links)]
df['coords']=coords
df['kws']=kws
df['cms']=cms

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-

In [26]:
df.to_csv('kozb.csv',sep=';')

In [70]:
df=pd.read_csv('kozb.csv',sep=';')

In [71]:
data=pd.DataFrame(df)

In [72]:
lat=[]
lon=[]
for i in range(len(data.index)):
    k=str(data.loc[data.index[i]]['coords']).replace("'",'').replace('[','')\
    .replace(']','').replace(' ','').split(',')
    lon.append(k[0])
    lat.append(k[1])

In [73]:
data['Latitude']=lat
data['Longitude']=lon

In [74]:
data=data.drop('coords',axis=1)
data=data[data.columns[2:]]

In [75]:
manual=data[data['Longitude']=='']
data=data[data['Longitude']!='']

In [76]:
data.to_excel('kdata.xlsx')
manual.to_excel('kmanual.xlsx')
manual.to_excel('kmanual_manual.xlsx')

Fix sector, address data and coordinates manually

In [77]:
data=pd.read_excel('kdata.xlsx')
manual=pd.read_excel('kmanual_manual.xlsx')

In [78]:
data=pd.concat([data.set_index('Közbirtokosság neve'),manual.set_index('Közbirtokosság neve')])

In [82]:
sectors=pd.read_excel('sectors.xlsx')
sectormap={}
repl={'á':'a','é':'e','í':'i','ó':'o','ú':'u','ü':'u','ű':'u','ő':'o','ö':'o'}
for s in sectors.columns:
    for k in sectors[s].values:
        for j in str(k).replace(' ','').split(','):
            sectormap[j]=s
            for c in repl:
                j=j.replace(c,repl[c])
            sectormap[j]=s

In [83]:
valid=[]
kws=[]
ki=-1
for i in range(len(data.index)):
    ks=data.loc[data.index[i]]['kws'].replace("'",'').replace('[','')\
                .replace(']','').replace(' ','').lower().split(',')[:-2]
    for k in ks:
        if k in sectormap:
            kws.append(sectormap[k])
            break
        k=k.replace('-','')
        if k in sectormap:
            kws.append(sectormap[k])
            break
    if len(kws)<i-1: 
        print('ERROR',ks,i)
        break
    else:
        #print('SUCCES',kws[-1],ks)
        valid.append([data.index[i],kws[-1],ks])

In [84]:
pd.DataFrame(valid).to_excel('kvalid.xlsx')
pd.DataFrame(valid).to_excel('kvalid_manual.xlsx')

Manual check and overwrite

In [161]:
manual=pd.read_excel('kmanual_manual.xlsx').set_index('Közbirtokosság neve')
data=pd.read_excel('kdata.xlsx').set_index('Közbirtokosság neve')
sectors=pd.read_excel('kvalid_manual.xlsx')

In [162]:
len(data), len(manual)

(23, 2)

In [163]:
data=pd.concat([data,manual])

In [164]:
data

Unnamed: 0 Helyezés.1  \
Közbirtokosság neve                                                         
GYERGYÓALFALUI KÖZBIRTOKOSSÁG/ COMPOSESORATUL J...           0          1   
ZETELAKI KÖZBIRTOKOSSÁG/ COMPOSESORAT ZETEA                  2          2   
SZOVÁTAI MAROS KÖZBIRTOKOSSÁG/ COMPOSESORATUL M...           3          3   
HOMORÓDALMÁSI KÖZBIRTOKOSSÁG/ COMPOSESORAT MERESTI           5         17   
CSÍKSZENTIMREI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOS...           6         11   
BORSZÉK KÖZBIRTOKOSSÁG GYERGYÓSZÁRHEGY/ COMPOSE...           7        >25   
CSÍKSZENTGYÖRGYI KÖZBIRTOKOSSÁG/ COMPOSESORATUL...           8          6   
GYERGYÓSZENTMIKLÓSI KÖZBIRTOKOSSÁG/ COMPOSESORA...           9          5   
KILYÉNFALVA KÖZBIRTOKOSSÁGA/ COMPOSESORATUL CHI...          10         20   
PAPOLCI IMREH ALBERT KÖZBIRTOKOSSÁG/ COMPOSESOR...          11          7   
CSÍKCSEKEFALVI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOS...          12          9   
CSÍKCSICSÓI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOSESO...          13         12   
NYÁRÁDREMETE KÖZBIRTOKOSSÁGA/ COMPOSESORATUL ER...          14         14   
CSÍKMADARASI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOSES...          15         15   
CSÍKSZENTMÁRTONI AKLOS KÖZBIRTOKOSSÁG/ ASOCIATI...          16        >25   
CSÍKSZENTDOMOKOSI KÖZBIRTOKOSSÁG/ ASOCIATIA COM...          17         10   
CSÍKBÁNKFALVI KÖZBIRTOKOSSÁG/ COMPOSESORATUL BANCU          18         19   
OZSDOLAI LÁROS TULAJDONOSI EGYESÜLET/ ASOCIATIE...          19        >25   
GYERGYÓCSOMAFALVA KÖZBIRTOKOSSÁGA/ COMPOSESORAT...          20        >25   
GYERGYÓÚJFALU KÖZBIRTOKOSSÁGA/ COMPOSESORATUL S...          21         13   
SZÉKELYSZÁLDOBOSI KÖZBIRTOKOSSÁG/ COMPOSESORAT ...          22        >25   
CSÍKSZENTKIRÁLYI KÖZBIRTOKOSSÁG/ ASOCIATIA COMP...          23         22   
CSÍKDÁNFALVI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOSES...          24        >25   
CSÍKJENŐFALVI TERCS KÖZBIRTOKOSSÁG/ ASOCIATIA C...           1         18   
GYERGYÓDITRÓI KÖZBIRTOKOSSÁG/ COMPOSESORATUL DI...           4         16   

                                                               Szék  \
Közbirtokosság neve                                                   
GYERGYÓALFALUI KÖZBIRTOKOSSÁG/ COMPOSESORATUL J...      Gyergyószék   
ZETELAKI KÖZBIRTOKOSSÁG/ COMPOSESORAT ZETEA           Udvarhelyszék   
SZOVÁTAI MAROS KÖZBIRTOKOSSÁG/ COMPOSESORATUL M...        Marosszék   
HOMORÓDALMÁSI KÖZBIRTOKOSSÁG/ COMPOSESORAT MERESTI    Udvarhelyszék   
CSÍKSZENTIMREI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOS...         Csíkszék   
BORSZÉK KÖZBIRTOKOSSÁG GYERGYÓSZÁRHEGY/ COMPOSE...      Gyergyószék   
CSÍKSZENTGYÖRGYI KÖZBIRTOKOSSÁG/ COMPOSESORATUL...         Csíkszék   
GYERGYÓSZENTMIKLÓSI KÖZBIRTOKOSSÁG/ COMPOSESORA...      Gyergyószék   
KILYÉNFALVA KÖZBIRTOKOSSÁGA/ COMPOSESORATUL CHI...      Gyergyószék   
PAPOLCI IMREH ALBERT KÖZBIRTOKOSSÁG/ COMPOSESOR...  Felső-Háromszék   
CSÍKCSEKEFALVI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOS...         Csíkszék   
CSÍKCSICSÓI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOSESO...         Csíkszék   
NYÁRÁDREMETE KÖZBIRTOKOSSÁGA/ COMPOSESORATUL ER...        Marosszék   
CSÍKMADARASI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOSES...         Csíkszék   
CSÍKSZENTMÁRTONI AKLOS KÖZBIRTOKOSSÁG/ ASOCIATI...         Csíkszék   
CSÍKSZENTDOMOKOSI KÖZBIRTOKOSSÁG/ ASOCIATIA COM...         Csíkszék   
CSÍKBÁNKFALVI KÖZBIRTOKOSSÁG/ COMPOSESORATUL BANCU         Csíkszék   
OZSDOLAI LÁROS TULAJDONOSI EGYESÜLET/ ASOCIATIE...  Felső-Háromszék   
GYERGYÓCSOMAFALVA KÖZBIRTOKOSSÁGA/ COMPOSESORAT...      Gyergyószék   
GYERGYÓÚJFALU KÖZBIRTOKOSSÁGA/ COMPOSESORATUL S...      Gyergyószék   
SZÉKELYSZÁLDOBOSI KÖZBIRTOKOSSÁG/ COMPOSESORAT ...   Alsó-Háromszék   
CSÍKSZENTKIRÁLYI KÖZBIRTOKOSSÁG/ ASOCIATIA COMP...         Csíkszék   
CSÍKDÁNFALVI KÖZBIRTOKOSSÁG/ ASOCIATIA COMPOSES...         Csíkszék   
CSÍKJENŐFALVI TERCS KÖZBIRTOKOSSÁG/ ASOCIATIA C...         Csíkszék   
GYERGYÓDITRÓI KÖZBIRTOKOSSÁG/ COMPOSESORATUL DI...      Gyergyószék   

                                                   Gaz

In [165]:
data['Sector']=sectors.set_index(0)[1]

In [166]:
data.columns

Index(['Unnamed: 0', 'Helyezés.1', 'Szék',
       'Gazdasági tevékenységbőlszármazó bevétel (RON)2018',
       'Gazdasági tevékenységbőlszármazó bevétel (RON)2017', 'kws', 'cms',
       'Latitude', 'Longitude', 'Sector'],
      dtype='object')

In [167]:
data=data[['Gazdasági tevékenységbőlszármazó bevétel (RON)2018',
       'Gazdasági tevékenységbőlszármazó bevétel (RON)2017', 'Szék',
       'Latitude', 'Longitude', 'Sector']]

In [168]:
data['Gazdasági tevékenységbőlszármazó bevétel (RON)2018']=\
    np.round(data['Gazdasági tevékenységbőlszármazó bevétel (RON)2018'].str.replace('\xa0','').astype(float)/1000000.0,3)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [169]:
data['Gazdasági tevékenységbőlszármazó bevétel (RON)2017']=\
    np.round(data['Gazdasági tevékenységbőlszármazó bevétel (RON)2017'].str.replace('\xa0','').astype(float)/1000000.0,3)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Pretty Names

In [170]:
data.index=data.index.str.title().str.split('/').str[0].str.replace('Közbirtokosság','KB').str.replace('KBa','KB').str.replace('KB','')

In [172]:
#overwrite sector
data['Sector']='Közbirtokosság'

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [177]:
data['Size']=data['Gazdasági tevékenységbőlszármazó bevétel (RON)2018']*5

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [178]:
data.to_excel('kexport.xlsx')

In [174]:
d2017=data[['Gazdasági tevékenységbőlszármazó bevétel (RON)2017']]
d2017.columns=['Gazdasági tevékenységbőlszármazó bevétel (millió RON)']
d2017['Év']=2017
d2018=data[['Gazdasági tevékenységbőlszármazó bevétel (RON)2018']]
d2018.columns=['Gazdasági tevékenységbőlszármazó bevétel (millió RON)']
d2018['Év']=2018
d2=pd.concat([d2017,d2018])

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [175]:
d2.join(data).to_excel('kexport2.xlsx')